In [47]:
# %pip install --upgrade --quiet  langchain langchain-community langchainhub langchain-openai langchain-chroma bs4

# %pip install --upgrade --quiet  langchain langchain-community
# ! pip install langchainhub
# ! pip install langchain-openai
# ! pip install langchain-chroma
# ! pip install bs4
# ! pip install jq

In [48]:
import re
import sys
import traceback
# import openai
from collections import deque
from openai import OpenAI

import configparser

# import networkx as nx
import logging
import time

import os
import requests
import networkx as nx
import pandas as pd
import geopandas as gpd
from pyvis.network import Network
 

import LLM_Find_Constants as constants
from langchain_core.prompts import ChatPromptTemplate


In [49]:
config = configparser.ConfigParser()
config.read('config.ini')

# use your KEY.
OpenAI_key = config.get('API_Key', 'OpenAI_key')

LangChain_API_key = config.get('API_Key', 'LangChain_API_key')
LangChain_API_key

'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'

In [53]:
from langchain_openai import ChatOpenAI

llm = ChatOpenAI(api_key=OpenAI_key, model="gpt-4o")
llm

ChatOpenAI(client=<openai.resources.chat.completions.Completions object at 0x000002B2D4053C50>, async_client=<openai.resources.chat.completions.AsyncCompletions object at 0x000002B2A680A5D0>, model_name='gpt-4o', openai_api_key=SecretStr('**********'), openai_proxy='')

  Using cached bs4-0.0.2-py2.py3-none-any.whl.metadata (411 bytes)
Using cached bs4-0.0.2-py2.py3-none-any.whl (1.2 kB)


In [64]:
import bs4
from langchain import hub
from langchain_chroma import Chroma
from langchain_community.document_loaders import WebBaseLoader
from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough
from langchain_openai import OpenAIEmbeddings
from langchain_text_splitters import RecursiveCharacterTextSplitter

# Load, chunk and index the contents of the blog.
loader = WebBaseLoader(
    web_paths=("https://api.census.gov/data/2021/acs/acs5/variables.html",),
    bs_kwargs=dict(
        parse_only=bs4.SoupStrainer()
    ),
)
docs = loader.load()

text_splitter = RecursiveCharacterTextSplitter(chunk_size=10000, chunk_overlap=2000)
splits = text_splitter.split_documents(docs)
vectorstore = Chroma.from_documents(documents=splits, embedding=OpenAIEmbeddings())

# Retrieve and generate using the relevant snippets of the blog.
retriever = vectorstore.as_retriever()
prompt = hub.pull("rlm/rag-prompt")


def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)






In [57]:
# format_docs(docs)

In [65]:
rag_chain = (
    {"context": retriever | format_docs, "question": RunnablePassthrough()}
    | prompt
    | llm
    | StrOutputParser()
)

In [70]:
results = rag_chain.invoke("You need to download the senior population (older than 65) data from US Census Bureau, what variables are needed? List all possible estimation variables, do not select variables ending with `M` or `MA`.")
print(results)

The variables needed are:

1. C21001H_013E
2. C21001H_014E
3. C21001H_015E
4. B01001A_029E
5. B01001A_030E
6. B01001A_031E


In [36]:
results = rag_chain.invoke("You need to download the higher education attainment population data, what variables is needed? List all possible estimation variables, do not select variables end with `M` or `MA`.")
print(results)

The possible estimation variables for higher education attainment population data are:

B15003_023E, B15003_024E, B15003_025E, B15011_001E, B15003_019E, B15003_020E, B15003_021E, B15003_022E, C15002A_009E, C15002A_010E, C15002A_011E, C15002B_001E, B15003_011E, B15003_012E, B15003_013E, B15003_014E, B15003_015E.


In [45]:
docs[0].page_content

'\n\n\nCensus Data API: /data/2019/acs/acs5/variables\n\n\n\n\n\n\n\n\n\n\n\n\nCensus Data API: Variables in /data/2019/acs/acs5/variables\n\n\n\nNameLabelConceptRequiredAttributesLimitPredicate TypeGroup\n\n\n\n\n27080 variables\n\n\n\n\nAIANHHGeographynot required0(not a predicate)\n\t\t\t\t\t\tN/A\n\t\t\t\t\t\n\n\nAIHHTLGeographynot required0(not a predicate)\n\t\t\t\t\t\tN/A\n\t\t\t\t\t\n\n\nAIRESGeographynot required0(not a predicate)\n\t\t\t\t\t\tN/A\n\t\t\t\t\t\n\n\nANRCGeographynot required0(not a predicate)\n\t\t\t\t\t\tN/A\n\t\t\t\t\t\n\n\nB01001_001EEstimate!!Total:SEX BY AGEnot requiredB01001_001EA,\n                B01001_001M,\n                B01001_001MA0longB01001\n\n\nB01001_002EEstimate!!Total:!!Male:SEX BY AGEnot requiredB01001_002EA,\n                B01001_002M,\n                B01001_002MA0longB01001\n\n\nB01001_003EEstimate!!Total:!!Male:!!Under 5 yearsSEX BY AGEnot requiredB01001_003EA,\n                B01001_003M,\n                B01001_003MA0longB01001\n\n

In [10]:
import getpass
import os

os.environ["OPENAI_API_KEY"] = getpass.getpass()

from langchain_openai import ChatOpenAI

llm = ChatOpenAI(model="gpt-4o", api_key=OpenAI_key)
llm

 ········


ChatOpenAI(client=<openai.resources.chat.completions.Completions object at 0x000002B29766CFB0>, async_client=<openai.resources.chat.completions.AsyncCompletions object at 0x000002B297674560>, model_name='gpt-4o', openai_api_key=SecretStr('**********'), openai_proxy='')

In [12]:
import bs4
from langchain import hub
from langchain_chroma import Chroma
from langchain_community.document_loaders import WebBaseLoader
from langchain_community.document_loaders import JSONLoader


from langchain_core.output_parsers import StrOutputParser
from langchain_core.runnables import RunnablePassthrough
from langchain_openai import OpenAIEmbeddings
from langchain_text_splitters import RecursiveCharacterTextSplitter

# Load, chunk and index the contents of the blog.

json_fname = r"E:\OneDrive_PSU\OneDrive - The Pennsylvania State University\Research_doc\LLM-Find\Census_variables.json"
loader = JSONLoader(
    file_path=json_fname,
    jq_schema='.messages[].content',
    text_content=False)

docs = loader.load()

docs

ImportError: jq package not found, please install it with `pip install jq`

In [11]:


text_splitter = RecursiveCharacterTextSplitter(chunk_size=1000, chunk_overlap=200)
splits = text_splitter.split_documents(docs)
vectorstore = Chroma.from_documents(documents=splits, embedding=OpenAIEmbeddings())

# Retrieve and generate using the relevant snippets of the blog.
retriever = vectorstore.as_retriever()
prompt = hub.pull("rlm/rag-prompt")


def format_docs(docs):
    return "\n\n".join(doc.page_content for doc in docs)


rag_chain = (
    {"context": retriever | format_docs, "question": RunnablePassthrough()}
    | prompt
    | llm
    | StrOutputParser()
)

rag_chain.invoke("What is Task Decomposition?")

'Task Decomposition is the process of breaking down a complicated task into smaller, more manageable steps. This can be done using techniques such as Chain of Thought (CoT) and Tree of Thoughts, which involve instructing a model to think step-by-step and explore multiple reasoning possibilities, respectively. The decomposition can be guided by simple prompting, task-specific instructions, or human input.'